In [1]:
import numpy as np
import os
import shutil
from sklearn.model_selection import train_test_split
import pandas as pd
import json 

Create train-test folder

In [3]:
base_path = 'kidney-ct-abnormality'
images_path = os.path.join(base_path, 'imagesTr')
all_images = [f for f in os.listdir(images_path) if f.endswith('.mha')]
train_files, test_files = train_test_split(all_images, test_size=0.2, random_state=219)

In [4]:
train_dir = os.path.join(base_path, 'train')
test_dir = os.path.join(base_path, 'test')
os.makedirs(train_dir, exist_ok=True)
os.makedirs(test_dir, exist_ok=True)

In [5]:
def move_files(files, destination):
    for f in files:
        shutil.move(os.path.join(images_path, f), os.path.join(destination, f))

In [6]:
move_files(train_files, train_dir)
move_files(test_files, test_dir)

Modify the json file

In [2]:
os.getcwd()

'/Users/ziyingye/Desktop/stats/24spring/STA663/kidney_CT_abnormality'

In [17]:
json_file_path = 'dataset.json' 
with open(json_file_path, 'r') as file:
    img_label = json.load(file)

In [18]:
data = img_label['training']
df = pd.DataFrame(data)
df.rename(columns={'Abnormality': 'abnormality'}, inplace=True)
df['image'] = df['image'].apply(lambda x: x[11:-4]+'_0000'+x[-4:])
test_images = [f for f in os.listdir('test') if f.endswith('.mha')]
df['split'] = df['image'].apply(lambda x: 'test' if x in test_images else 'train')
df

image  abnormality  split
0    kidneyabnormalityKiTS-0000_0000.mha            0  train
1    kidneyabnormalityKiTS-0001_0000.mha            1  train
2    kidneyabnormalityKiTS-0002_0000.mha            0  train
3    kidneyabnormalityKiTS-0003_0000.mha            1   test
4    kidneyabnormalityKiTS-0004_0000.mha            1   test
..                                   ...          ...    ...
981  kidneyabnormalityRUMC-0390_0000.mha            0   test
982  kidneyabnormalityRUMC-0391_0000.mha            0  train
983  kidneyabnormalityRUMC-0392_0000.mha            0  train
984  kidneyabnormalityRUMC-0393_0000.mha            0   test
985  kidneyabnormalityRUMC-0394_0000.mha            0  train

[986 rows x 3 columns]

In [20]:
df_copy = df.copy()
df_copy['count']=1
df_copy.groupby(['split', 'abnormality']).sum()

count
split abnormality       
test  0               79
      1              119
train 0              289
      1              499

In [22]:
list_of_dicts = df.to_dict(orient='records')
list_of_dicts

[{'image': 'kidneyabnormalityKiTS-0000_0000.mha',
  'abnormality': 0,
  'split': 'train'},
 {'image': 'kidneyabnormalityKiTS-0001_0000.mha',
  'abnormality': 1,
  'split': 'train'},
 {'image': 'kidneyabnormalityKiTS-0002_0000.mha',
  'abnormality': 0,
  'split': 'train'},
 {'image': 'kidneyabnormalityKiTS-0003_0000.mha',
  'abnormality': 1,
  'split': 'test'},
 {'image': 'kidneyabnormalityKiTS-0004_0000.mha',
  'abnormality': 1,
  'split': 'test'},
 {'image': 'kidneyabnormalityKiTS-0005_0000.mha',
  'abnormality': 1,
  'split': 'train'},
 {'image': 'kidneyabnormalityKiTS-0006_0000.mha',
  'abnormality': 0,
  'split': 'train'},
 {'image': 'kidneyabnormalityKiTS-0007_0000.mha',
  'abnormality': 1,
  'split': 'train'},
 {'image': 'kidneyabnormalityKiTS-0008_0000.mha',
  'abnormality': 1,
  'split': 'train'},
 {'image': 'kidneyabnormalityKiTS-0009_0000.mha',
  'abnormality': 0,
  'split': 'train'},
 {'image': 'kidneyabnormalityKiTS-0010_0000.mha',
  'abnormality': 1,
  'split': 'train'},
 

In [23]:
df.to_json('dataset_m.json', orient='records', lines=True)